In [1]:
from sentence_transformers import SentenceTransformer, util
import pandas as pd
import re

/Users/satoc/miniforge3/envs/gradio/lib/python3.12/site-packages/sentence_transformers/cross_encoder/CrossEncoder.py:13: TqdmExperimentalWarning: Using `tqdm.autonotebook.tqdm` in notebook mode. Use `tqdm.tqdm` instead to force console mode (e.g. in jupyter console)
  from tqdm.autonotebook import tqdm, trange


In [76]:
# Target列を分割する関数
def split_target(target):
    # 指定された区切り文字で分割
    split_words = re.split(r'[,\n、・及びおよび又はまたは]+', target)
    # 空白文字を除外してリストとして返す
    return [word.strip() for word in split_words if word.strip()]


# Target列を分割する関数（改良後）
def split_target_English(target):
    # 区切り文字を (,) or (\n) or (、) or (・) または文字列"or" として扱う
    # 正規表現では、パイプ(|)でor条件を定義し、"(?: ... )"はグルーピングのみ行う非捕捉グループ
    # [,\n、・] はいずれかの1文字とマッチ
    # or は文字列全体とマッチ
    # 複数連続した区切り文字をまとめて1回の分割として扱うために+(1回以上)とする
    split_words = re.split(r'(?:[,\n、・]|or| and)+', target)
    
    # 空白文字を除外してリストとして返す
    return [word.strip() for word in split_words if word.strip()]

# 処理プログラム
def split_triple_negative_words(target_words):
    updated_words = []
    for word in target_words:
        if 'triple negative' in word.lower():
            # 'triple negative' の部分を追加
            updated_words.append('Triple Negative')  # 大文字で統一して追加
            # 'triple negative' を除いた残りの部分を追加
            remaining = word.lower().replace('triple negative', '').strip()
            if remaining:  # 残りの単語が存在する場合のみ追加
                updated_words.append(remaining.title().strip())  # 単語の先頭を大文字化
        else:
            updated_words.append(word.strip().title())  # 単語の先頭を大文字化
    return updated_words

class WordProcessor:
    def __init__(self, target_words):
        self.target_words = target_words

    def process(self, target_words):
        """
        入力された単語のリストを処理して、ターゲット単語に基づき分割します。
        """
        updated_words = []
        for word in target_words:
            word_lower = word.lower()
            for target in self.target_words:
                if target in word_lower:
                    # ターゲット単語を追加
                    updated_words.append(target.title())
                    # ターゲット単語を除いた残りを追加
                    remaining = word_lower.replace(target, '').strip()
                    if remaining:
                        updated_words.append(remaining.title())
                    break
            else:
                # ターゲット単語に該当しない場合
                updated_words.append(word.strip().title())
        return updated_words

    def __call__(self, target_words):
        """
        インスタンスを関数として呼び出すためのエントリポイント。
        """
        return self.process(target_words)


In [77]:
exclusive_words = ["triple negative", "double positive"]

    # インスタンス作成
processor = WordProcessor(exclusive_words)

In [78]:
basedf = pd.read_csv('../ClinicalTrialCSV/JRCT20241215Cancer.csv', index_col=0)
basedf = basedf.dropna(subset=['試験等のフェーズ'])
# Target列を分割してTargetWord列を追加
basedf['TargetWord'] = basedf['TargetEnglish'].apply(split_target_English)
# 各行のTargetWord列に処理を適用
# NaN や None の場合の処理を追加
basedf['TargetWord'] = basedf['TargetWord'].apply(lambda x: processor(x) if isinstance(x, list) else x)

In [79]:
basedf.dropna(subset=['TargetEnglish'])

JRCT ID       NCT No      JapicCTI No  \
0    jRCT2031240552  NCT06599502              NaN   
3    jRCT2031240547          NaN              NaN   
5    jRCT2031240542          NaN              NaN   
7    jRCT2031240536  NCT06003231              NaN   
9    jRCT2031240530          NaN              NaN   
..              ...          ...              ...   
729  jRCT2031200057          NaN              NaN   
739  jRCT2073200004          NaN              NaN   
760  jRCT2033190086          NaN              NaN   
762  jRCT2031190072          NaN              NaN   
772  jRCT2051190009  NCT03818893  JapicCTI-194618   

                                                 Title  \
0    KRAS G12D 変異陽性がん患者を対象としてAZD0022 の単剤療法及び抗がん剤との併...   
3    FGFR2b陽性切除不能進行・再発の胃または食道胃接合部腺癌を対象としたBemarituzu...   
5    自家造血幹細胞移植非適応の初発多発性骨髄腫患者を対象としてベランタマブ マホドチンとレナリド...   
7    既治療の局所進行切除不能又は転移性HER2発現固形癌を有する成人患者を対象としたDisita...   
9    HER2遺伝子増幅あるいはHER2遺伝子変異を有するII-III期非小細胞肺癌に対するTra...   
..                                                 ...   
729      治療抵抗性乳がんを対象としたTDM-812の腫瘍内投与法の安全性評価を目的とした第I相試験   
739            切除不能膵癌を対象とした腫瘍溶解性ウイルスの腫瘍内局所投与の臨床第Ⅰ/Ⅱ相試験   
760  悪性黒色腫患者を対象としたインターロイキン12発現型遺伝子組換え単純ヘルペスウイルス１型の第...   
762                  切除不能な進行肝細胞癌患者を対象としたCYT001の第I相臨床試験   
772  進行性悪性黒色腫患者を対象としたGEN0101の皮内投与と、ペムブロリズマブ（抗PD-1抗体...   

                                               TargetJ  \
0                 以下の進行固形がん患者\n・非小細胞肺癌\n・膵管腺癌\n・結腸・直腸癌   
3                               切除不能進行・再発の胃または食道胃接合部腺癌   
5                                               多発性骨髄腫   
7                            頭頸部扁平上皮癌、非小細胞肺癌、卵巣癌、子宮内膜癌   
9    HER2遺伝子増幅あるいはHER2遺伝子変異を有するII/IIIA/IIIB(T3-4N2)...   
..                                                 ...   
729                                                乳がん   
739                                                 膵癌   
760                                              悪性黒色腫   
762                                               肝細胞癌   
772                                           進行性悪性黒色腫   

                                                Target  \
0                    以下の進行固形がん患者 ・非小細胞肺癌 ・膵管腺癌 ・結腸・直腸癌   
3                               切除不能進行・再発の胃または食道胃接合部腺癌   
5                                               多発性骨髄腫   
7                            頭頸部扁平上皮癌、非小細胞肺癌、卵巣癌、子宮内膜癌   
9    HER2遺伝子増幅あるいはHER2遺伝子変異を有するII/IIIA/IIIB(T3-4N2)...   
..                                                 ...   
729                                                乳がん   
739                                                 膵癌   
760                                              悪性黒色腫   
762                                               肝細胞癌   
772                                           進行性悪性黒色腫   

                                         TargetEnglish  \
0    Non-Small Cell Lung Cancer (NSCLC) Pancreatic ...   
3    Advanced Gastric or Gastroesophageal Junction ...   
5                                     Multiple Myeloma   
7    Head and neck squamous cell carcinoma/Non-smal...   
9    Stage II-III HER2-Amplified or HER2-Mutant Non...   
..                                                 ...   
729                                      Breast cancer   
739                                  Pancreatic cancer   
760                                 malignant melanoma   
762                           Hepatocellular carcinoma   
772                                  advanced melanoma   

                                              研究・治験の目的 試験等のフェーズ 試験の種類  ...  \
0                                            Treatment      1-2   NaN  ...   
3    フッ化ピリミジン系薬剤に不応または不耐となったFGFR2b陽性の切除不能進行・再発の胃腺癌又...        2   NaN  ...   
5    自家造血幹細胞移植非適応の初発多発性骨髄腫を対象にGSK2857916、レナリドミド 及び ...        3   NaN  ...   
7    既治療の局所進行切除不能又は転移性(LA/m)ヒト上皮増殖因子受容体2型(HER2)発現固形...        2   NaN  ...   
9    HER2遺伝子増幅あるいはHER2遺伝子変異を有するII/IIIA/IIIB(T3-4N2)...        2   NaN  ...   
..                                                 ...      ...   ...  ...   
729  TDM-812の腫瘍内投与の安全性および忍容性を評価し、今後の臨床評価に

In [80]:
print(basedf[basedf['JRCT ID'] == 'jRCT2031230090']['TargetWord'])
print(basedf[basedf['JRCT ID'] == 'jRCT2031230090']['TargetEnglish'])
print(basedf[basedf['JRCT ID'] == 'jRCT2031230090']['Exclusion Criteria'])

391    [Relapsed/Refract, Y Locally Advanced, Metasta...
Name: TargetWord, dtype: object
391    Relapsed/Refractory Locally Advanced or Metast...
Name: TargetEnglish, dtype: object
391    Dose Escalation and Expansion Cohorts 1. Women...
Name: Exclusion Criteria, dtype: object


In [81]:
# 値を直接取得して表示
print(basedf.loc[basedf['JRCT ID'] == 'jRCT2031230090', 'TargetWord'].values[0])
print(basedf.loc[basedf['JRCT ID'] == 'jRCT2031230090', 'TargetEnglish'].values[0])
print(basedf.loc[basedf['JRCT ID'] == 'jRCT2031230090', 'Exclusion Criteria'].values[0])


['Relapsed/Refract', 'Y Locally Advanced', 'Metastatic Breast Cancer', 'Triple Negative', 'Breast Cancer']
Relapsed/Refractory Locally Advanced or Metastatic Breast Cancer and Triple Negative Breast Cancer
Dose Escalation and Expansion Cohorts 1. Women who are pregnant or lactating. Women of child-bearing potential (WOCBP) not using adequate birth control see Appendix H: Forms of contraception. 2. Patients with known central nervous system (CNS) or leptomeningeal metastases not controlled by prior surgery, radiotherapy or requiring corticosteroids to control symptoms, or patients with symptoms suggesting CNS involvement for which treatment is required. 3. Patients with primary brain tumors. 4. Patients with any hematologic malignancy. This includes leukemia (any form), lymphoma, and multiple myeloma. 5. Patients with any of the following hematologic abnormalities at baseline. (Patients may have received a red blood cell product transfusion prior to study, if clinically warranted.): -Ab

In [82]:
# モデルのロード
model = SentenceTransformer('pritamdeka/S-PubMedBert-MS-MARCO')

/Users/satoc/miniforge3/envs/gradio/lib/python3.12/site-packages/transformers/tokenization_utils_base.py:1617: FutureWarning: `clean_up_tokenization_spaces` was not set. It will be set to `True` by default. This behavior will be deprecated in transformers v4.45, and will be then set to `False` by default. For more details check this issue: https://github.com/huggingface/transformers/issues/31884
  warnings.warn(


In [89]:
# クエリ
#query = "Triple negative breast cancer"
query = "breast cancer"
#query = "glioma"
threshold = 0.925
# クエリをベクトル化
query_vec = model.encode(query, convert_to_tensor=True)


In [90]:
# ターゲットリスト全体を処理
matched_indices = []
target_vecs_list = []
cosine_scores_list = []
for idx, target_words in enumerate(basedf['TargetWord']):
    # ターゲット内の各単語をベクトル化
    target_vecs = model.encode(target_words, convert_to_tensor=True)
    # コサイン類似度を計算
    cosine_scores = util.cos_sim(query_vec, target_vecs).squeeze()
    target_vecs_list.append(target_vecs)
    cosine_scores_list.append(cosine_scores)
    # 閾値を超えるか確認
    if (cosine_scores >= threshold).any():  # いずれかが閾値を超えている場合
        matched_indices.append(idx)

# 抽出
matched_df = basedf.iloc[matched_indices]
matched_df

JRCT ID       NCT No JapicCTI No  \
31   jRCT2061240081  NCT06393374         NaN   
157  jRCT2052240059          NaN         NaN   
170  jRCT2031240096  NCT06380751         NaN   
215  jRCT2031230723  NCT06112379         NaN   
240  jRCT2061230102  NCT06103864         NaN   
307  jRCT2061230074  NCT05952557         NaN   
351  jRCT2031230279  NCT05862285         NaN   
388  jRCT2031230109  NCT05514054         NaN   
391  jRCT2031230090          NaN         NaN   
392  jRCT2031230096  NCT05774951         NaN   
402  jRCT2061230009  NCT05485766         NaN   
463  jRCT2061220087  NCT05629585         NaN   
515  jRCT2031220276  NCT05307705         NaN   
590  jRCT2031210585  NCT05123482         NaN   
593  jRCT2031210560  NCT05061823         NaN   
629  jRCT2052210099          NaN         NaN   
698  jRCT2071200086  NCT04640623         NaN   
729  jRCT2031200057          NaN         NaN   

                                                 Title  \
31   術前薬物療法後の手術時に病理学的完全奏効を達成していないトリプルネガティブ乳癌患者を対象に、...   
157  遺伝子HSD17B4高メチル化を有するHER2陽性ER陰性乳癌における非手術療法の有用性を評...   
170  本治験の主要目的は、BRCA1、BRCA2 又は PALB2 変異を有し、HR 陽性、HER...   
215  未治療のトリプルネガティブ又はホルモン受容体低発現／HER2陰性乳癌の成人患者を対象として、...   
240  Programmed death-ligand（PD-L1）陽性の局所再発手術不能又は転移性...   
307  根治的局所治療（化学療法の併用または非併用）を受けて疾患の兆候のない、再発リスクが中間～高リ...   
351  GENENTECH社及び／又はF.HOFFMANN-LA ROCHE LTDが依頼した試験に...   
388  EMBER-4：2～5年間の術後内分泌療法による前治療歴を有する再発高リスクのER+、HER...   
391  MELK阻害剤OTS167POにおける転移性・進行性乳がん患者を対象とした安全性、忍容性およ...   
392  根治的局所領域療法（化学療法の併用または非併用）および標準補助内分泌療法（ET）を少なくとも...   
402  gBRCA1/2遺伝子変異を有するトリプルネガティブ原発乳がんに対するプラチナ製剤、PARP...   
463  術前薬物療法後の外科的切除時に乳房及び／又は腋窩リンパ節に浸潤性残存病変を有するステージI～...   
515  PIK3CA H1047R変異を有する進行乳がん患者及びその他の固形がん患者を対象としたLO...   
590  進行又は転移性固形がん患者を対象としたAZD8205の単独療法及び他の抗がん剤との併用療法に...   
593  複数のBintrafusp alfa（M7824）臨床試験の被験者を対象に長期データを収集す...   
629  乳がんを有する成人女性及び健康成人女性を対象とした乳房用マイクロ波画像診断装置IGS-000...   
698  膀胱全摘除術に不適格である，又は膀胱全摘除術を選択しなかった，カルメット・ゲラン桿菌（BCG...   
729      治療抵抗性乳がんを対象としたTDM-812の腫瘍内投与法の安全性評価を目的とした第I相試験   

                               TargetJ                             Target  \
31                         トリプルネガティブ乳癌                        トリプルネガティブ乳癌   
157                                乳がん                                乳がん   
170                               進行乳癌                               進行乳癌   
215                                 乳癌                                 乳癌   
240                                 乳癌                                 乳癌   
307                          乳がん、早期乳がん                          乳がん、早期乳がん   
351                                  癌                                  癌   
388                                 乳癌                                 乳癌   
391  再発・難治性の局所進行性・転移性乳がん及びトリプルネガティブ乳がん  再発・難治性の局所進行性・転移性乳がん及びトリプルネガティブ乳がん   
392                          乳がん、早期乳がん                          乳がん、早期乳がん   
402                       トリプルネガティブ乳がん                       トリプルネガティブ乳がん   
463                                 乳癌                                 乳癌   
515                                乳がん                                乳がん   
590                   乳癌、胆道癌、卵巣癌、子宮内膜癌                   乳癌、胆道癌、卵巣癌、子宮内膜癌   
593                                固形癌                                固形癌   
629                                乳がん                                乳がん   
698                                膀胱癌                                膀胱癌   
729                                乳がん                                乳がん   

                                         TargetEnglish  \
31                       Triple negative breast cancer   
157                                      Breast cancer   
170                             Advanced Breast Cancer   
215                                      Breast Cancer   
240                                      Breast Cancer   
307                 Breast Cancer, Early Breast Cancer   
351                                             Cancer   
388                                   Breast Neoplasms   
391  Relap

In [92]:
cosine_scores_list [matched_indices]

TypeError: list indices must be integers or slices, not list

In [86]:
# ターゲットリスト全体を処理
matched_indices = []
target_vecs_list = []
cosine_scores_list = []
for idx, target_words in enumerate(basedf['TargetWord']):
    # ターゲット内の各単語をベクトル化
    target_vecs = model.encode(target_words, convert_to_tensor=True)
    # コサイン類似度を計算
    cosine_scores = util.cos_sim(query_vec, target_vecs).squeeze()
    target_vecs_list.append(target_vecs)
    cosine_scores_list.append(cosine_scores)
    # 閾値を超えるか確認
    if (cosine_scores >= threshold).any():  # いずれかが閾値を超えている場合
        matched_indices.append(idx)

# 抽出
matched_df = basedf.iloc[matched_indices]
matched_df

JRCT ID       NCT No JapicCTI No  \
31   jRCT2061240081  NCT06393374         NaN   
157  jRCT2052240059          NaN         NaN   
215  jRCT2031230723  NCT06112379         NaN   
240  jRCT2061230102  NCT06103864         NaN   
307  jRCT2061230074  NCT05952557         NaN   
388  jRCT2031230109  NCT05514054         NaN   
391  jRCT2031230090          NaN         NaN   
392  jRCT2031230096  NCT05774951         NaN   
402  jRCT2061230009  NCT05485766         NaN   
463  jRCT2061220087  NCT05629585         NaN   
515  jRCT2031220276  NCT05307705         NaN   
590  jRCT2031210585  NCT05123482         NaN   
629  jRCT2052210099          NaN         NaN   
729  jRCT2031200057          NaN         NaN   

                                                 Title  \
31   術前薬物療法後の手術時に病理学的完全奏効を達成していないトリプルネガティブ乳癌患者を対象に、...   
157  遺伝子HSD17B4高メチル化を有するHER2陽性ER陰性乳癌における非手術療法の有用性を評...   
215  未治療のトリプルネガティブ又はホルモン受容体低発現／HER2陰性乳癌の成人患者を対象として、...   
240  Programmed death-ligand（PD-L1）陽性の局所再発手術不能又は転移性...   
307  根治的局所治療（化学療法の併用または非併用）を受けて疾患の兆候のない、再発リスクが中間～高リ...   
388  EMBER-4：2～5年間の術後内分泌療法による前治療歴を有する再発高リスクのER+、HER...   
391  MELK阻害剤OTS167POにおける転移性・進行性乳がん患者を対象とした安全性、忍容性およ...   
392  根治的局所領域療法（化学療法の併用または非併用）および標準補助内分泌療法（ET）を少なくとも...   
402  gBRCA1/2遺伝子変異を有するトリプルネガティブ原発乳がんに対するプラチナ製剤、PARP...   
463  術前薬物療法後の外科的切除時に乳房及び／又は腋窩リンパ節に浸潤性残存病変を有するステージI～...   
515  PIK3CA H1047R変異を有する進行乳がん患者及びその他の固形がん患者を対象としたLO...   
590  進行又は転移性固形がん患者を対象としたAZD8205の単独療法及び他の抗がん剤との併用療法に...   
629  乳がんを有する成人女性及び健康成人女性を対象とした乳房用マイクロ波画像診断装置IGS-000...   
729      治療抵抗性乳がんを対象としたTDM-812の腫瘍内投与法の安全性評価を目的とした第I相試験   

                               TargetJ                             Target  \
31                         トリプルネガティブ乳癌                        トリプルネガティブ乳癌   
157                                乳がん                                乳がん   
215                                 乳癌                                 乳癌   
240                                 乳癌                                 乳癌   
307                          乳がん、早期乳がん                          乳がん、早期乳がん   
388                                 乳癌                                 乳癌   
391  再発・難治性の局所進行性・転移性乳がん及びトリプルネガティブ乳がん  再発・難治性の局所進行性・転移性乳がん及びトリプルネガティブ乳がん   
392                          乳がん、早期乳がん                          乳がん、早期乳がん   
402                       トリプルネガティブ乳がん                       トリプルネガティブ乳がん   
463                                 乳癌                                 乳癌   
515                                乳がん                                乳がん   
590                   乳癌、胆道癌、卵巣癌、子宮内膜癌                   乳癌、胆道癌、卵巣癌、子宮内膜癌   
629                                乳がん                                乳がん   
729                                乳がん                                乳がん   

                                         TargetEnglish  \
31                       Triple negative breast cancer   
157                                      Breast cancer   
215                                      Breast Cancer   
240                                      Breast Cancer   
307                 Breast Cancer, Early Breast Cancer   
388                                   Breast Neoplasms   
391  Relapsed/Refractory Locally Advanced or Metast...   
392                 Breast Cancer, Early Breast Cancer   
402                   Triple Negative Breast Neoplasms   
463                                      Breast Cancer   
515                                      Breast Cancer   
590  Breast Cancer, Biliary Tract Carcinoma, Ovaria...   
629                                      Breast cancer   
729                                      Breast cancer   

                                              研究・治験の目的 試験等のフェーズ 試験の種類  ...  \
31   術前薬物療法後の手術時に病理学的完全奏効を達成していないトリプルネガティブ乳癌患者を対象に、...        3   NaN  ...   
157  HSD17B4高メチル化(HSD17B4 hypermethylation:HH)を有するH...        2   NaN  ...   
215  未治療のトリプルネガティブ又はホルモン受容体低発現/HER2陰性乳癌の成人患者を対象として、...        3   NaN  ...   
240  PD-L1陽性の局所再発手術不能または転移性TNBC患者を対象に、デュルバルマブ併用または非...        3   NaN  ...   
307

In [14]:
# 全データのターゲット列をベクトル化
target_list = basedf['TargetEnglish'].tolist()
target_vecs = model.encode(target_list, convert_to_tensor=True)
# コサイン類似度を計算
cosine_scores = util.cos_sim(query_vec, target_vecs).squeeze()

In [15]:
matched_indices_d = (cosine_scores >= threshold).nonzero().tolist()
# 入れ子リストをフラットなリストに変換
flat_indices_d = [idx[0] for idx in matched_indices_d]

# 抽出
matched_df_d = basedf.iloc[flat_indices_d]
matched_df_d


JRCT ID       NCT No JapicCTI No  \
157  jRCT2052240059          NaN         NaN   
170  jRCT2031240096  NCT06380751         NaN   
215  jRCT2031230723  NCT06112379         NaN   
240  jRCT2061230102  NCT06103864         NaN   
307  jRCT2061230074  NCT05952557         NaN   
342  jRCT2051230094  NCT05794906         NaN   
351  jRCT2031230279  NCT05862285         NaN   
388  jRCT2031230109  NCT05514054         NaN   
392  jRCT2031230096  NCT05774951         NaN   
463  jRCT2061220087  NCT05629585         NaN   
515  jRCT2031220276  NCT05307705         NaN   
593  jRCT2031210560  NCT05061823         NaN   
600  jRCT2041210123  NCT05114746         NaN   
629  jRCT2052210099          NaN         NaN   
691  jRCT2031200384  NCT04221542         NaN   
698  jRCT2071200086  NCT04640623         NaN   
729  jRCT2031200057          NaN         NaN   

                                                 Title    TargetJ     Target  \
157  遺伝子HSD17B4高メチル化を有するHER2陽性ER陰性乳癌における非手術療法の有用性を評...        乳がん        乳がん   
170  本治験の主要目的は、BRCA1、BRCA2 又は PALB2 変異を有し、HR 陽性、HER...       進行乳癌       進行乳癌   
215  未治療のトリプルネガティブ又はホルモン受容体低発現／HER2陰性乳癌の成人患者を対象として、...         乳癌         乳癌   
240  Programmed death-ligand（PD-L1）陽性の局所再発手術不能又は転移性...         乳癌         乳癌   
307  根治的局所治療（化学療法の併用または非併用）を受けて疾患の兆候のない、再発リスクが中間～高リ...  乳がん、早期乳がん  乳がん、早期乳がん   
342  前立腺癌の高リスク生化学的再発（BCR）患者を対象としたアンドロゲン遮断療法（ADT）を併用...       前立腺癌       前立腺癌   
351  GENENTECH社及び／又はF.HOFFMANN-LA ROCHE LTDが依頼した試験に...          癌          癌   
388  EMBER-4：2～5年間の術後内分泌療法による前治療歴を有する再発高リスクのER+、HER...         乳癌         乳癌   
392  根治的局所領域療法（化学療法の併用または非併用）および標準補助内分泌療法（ET）を少なくとも...  乳がん、早期乳がん  乳がん、早期乳がん   
463  術前薬物療法後の外科的切除時に乳房及び／又は腋窩リンパ節に浸潤性残存病変を有するステージI～...         乳癌         乳癌   
515  PIK3CA H1047R変異を有する進行乳がん患者及びその他の固形がん患者を対象としたLO...        乳がん        乳がん   
593  複数のBintrafusp alfa（M7824）臨床試験の被験者を対象に長期データを収集す...        固形癌        固形癌   
600  進行性PSMA陽性転移性去勢抵抗性前立腺がん（mCRPC）を有する患者を対象に177Lu-P...       前立腺癌       前立腺癌   
629  乳がんを有する成人女性及び健康成人女性を対象とした乳房用マイクロ波画像診断装置IGS-000...        乳がん        乳がん   
691  転移性去勢抵抗性前立腺がん患者を対象としたAMG 509の安全性、忍容性、薬物動態及び有効性...      前立腺がん      前立腺がん   
698  膀胱全摘除術に不適格である，又は膀胱全摘除術を選択しなかった，カルメット・ゲラン桿菌（BCG...        膀胱癌        膀胱癌   
729      治療抵抗性乳がんを対象としたTDM-812の腫瘍内投与法の安全性評価を目的とした第I相試験        乳がん        乳がん   

                          TargetEnglish  \
157                       Breast cancer   
170              Advanced Breast Cancer   
215                       Breast Cancer   
240                       Breast Cancer   
307  Breast Cancer, Early Breast Cancer   
342                     prostate cancer   
351                              Cancer   
388                    Breast Neoplasms   
392  Breast Cancer, Early Breast Cancer   
463                       Breast Cancer   
515                       Breast Cancer   
593                              Cancer   
600                     Prostate Cancer   
629                       Breast cancer   
691                     Prostate Cancer   
698                      Bladder Cancer   
729                       Breast cancer   

                                              研究・治験の目的 試験等のフェーズ 試験の種類  ...  \
157  HSD17B4高メチル化(HSD17B4 hypermethylation:HH)を有するH...        2   NaN  ...   
170                                          Treatment        3   NaN  ...   
215  未治療のトリプルネガティブ又はホルモン受容体低発現/HER2陰性乳癌の成人患者を対象として、...        3   NaN  ...   
240  PD-L1陽性の局所再発手術不能または転移性TNBC患者を対象に、デュルバルマブ併用または非...        3   NaN  ...   
307                                          Treatment        3   NaN  ...   
342  BAY 1841788(darolutamide)とADTの24ヵ月間併用投与によって、プラ...        3   NaN  ...   
351  本継続投与試験の目的は,親治験から移行する時点でまだ治験治療を受けており,その地域でその治療...        3   NaN  ...   
388            早期乳癌患者を対象としたimlunestrantと標準的な内分泌療法の比較試験        3   NaN  ...   
392                                          Treatment        3   NaN  ...   
463  術前薬物療法後の外科的切除時に乳房および/または腋窩リンパ節に浸潤性残存病変を有するI~II...        3   NaN  ...   
515  LOXO-783 の単独投与及び他の抗がん剤との併用投与における 第 2 相試験の推奨用量、...        1   NaN  ..